In [86]:
import plotly.express as px
import pandas as pd
import numpy as np
from datetime import datetime

# Dados do dia 19/05
df = pd.read_csv('data-19-05-Vanessa.csv')

# transforma o índice em datetime
df.index = pd.to_datetime(df['index'], format='%Y-%m-%dT%H:%M:%S.%f')
df.drop(columns=['index'], inplace=True)

df.head()

p00  p01  p02  p03  p04  p05  p06  p07  p08  p09  \
index                                                                       
2023-05-19 14:11:45.149    0    0    0    0    0    0    0  499    0    0   
2023-05-19 14:11:46.149    0    0    0    0    0    0    0  204    0    0   
2023-05-19 14:11:46.649    0    0    0    0    0    0    0  251    0    0   
2023-05-19 14:11:47.149    0    0    0    0    0    0    0  191    0    0   
2023-05-19 14:11:47.649    0    0    0    0    0    0    0  192    0    0   

                         p10  p11  
index                              
2023-05-19 14:11:45.149    0    0  
2023-05-19 14:11:46.149    0    0  
2023-05-19 14:11:46.649    0    0  
2023-05-19 14:11:47.149    0    0  
2023-05-19 14:11:47.649    0    0

In [87]:
# Captura poses Vanessa
df_poses_vanessa = df.iloc[14:7448-274, :]
# px.line(df_poses_vanessa, x=df_poses_vanessa.index, y=df_poses_vanessa.columns)

# Captura poses Bruno
df_poses_bruno = df.iloc[7509-274:16398-274, :]

# Dados captura Laguardia
df_poses_laguardia = pd.read_csv('data.csv')

# Captura poses Laguardia
df_poses_laguardia.index = pd.to_datetime(df_poses_laguardia['index'], format='%Y-%m-%dT%H:%M:%S.%f')
df_poses_laguardia.drop(columns=['index'], inplace=True)
df_poses_laguardia = df_poses_laguardia.iloc[8750:, :]

In [88]:
# script de detecção de poses

import pprint  # print bonito pra mostrar o resultado

def seated(data) -> bool:
    """
    Regras para dizer se o usuário está sentado ou não.
    """
    return not(data['p00'] < 10 and data['p01'] < 10 and data['p05'] < 10 and data['p06'] < 10)


def check_poses(df) -> dict:
    """
    Função que recebe um dataframe e retorna um dicionário
    com os índices de início e fim de cada pose.
    """

    poses = {}                      # dicionário de poses
    pose_atual = 1                  # pose atual
    first_seat = None               # primeiro índice em que o usuário estava sentado
    seated_frames_threshold = 10    # número de frames que o usuário deve estar em pé para considerar que ele está sentado

    seated_frames = 0
    for line in df.iterrows():
        index, data = line

        if seated(data):
            # se a pose atual já foi registrada, continua
            if pose_atual in poses:
                continue
            
            # se o usuário estava em pé, define o índice de início da pose atual
            if seated_frames == 0:
                first_seat = index
            seated_frames += 1
            
            # se o número de frames em que o usuário está sentado superar o threshold,
            # considera que ele está sentado e marca o índice de início da pose atual
            if seated_frames > seated_frames_threshold:
                poses[pose_atual] = {}
                poses[pose_atual]['start'] = first_seat
        
        else:  # não está sentado
            seated_frames = 0
            # se o usuário estava sentado, marca o índice de fim da pose atual
            if pose_atual in poses:
                if 'end' not in poses[pose_atual]:
                    poses[pose_atual]['end'] = index
                    pose_atual += 1  # vai para a próxima pose
    
    return poses


# Poses para cada um
poses_vanessa = check_poses(df_poses_vanessa)
poses_bruno = check_poses(df_poses_bruno)
poses_laguardia = check_poses(df_poses_laguardia)

In [89]:
# script de detecção de poses

import pprint  # print bonito pra mostrar o resultado

def seated(data) -> bool:
    """
    Regras para dizer se o usuário está sentado ou não.
    """
    return not(data['p00'] < 10 and data['p01'] < 10 and data['p05'] < 10 and data['p06'] < 10)


def check_poses_vanessa(df) -> dict:
    """
    Função que recebe um dataframe e retorna um dicionário
    com os índices de início e fim de cada pose.
    """

    poses = {}                      # dicionário de poses
    pose_atual = 1                  # pose atual
    first_seat = None               # primeiro índice em que o usuário estava sentado
    seated_frames_threshold = 10    # número de frames que o usuário deve estar em pé para considerar que ele está sentado

    seated_frames = 0
    for line in df.iterrows():
        index, data = line

        if seated(data):
            # se a pose atual já foi registrada, continua
            if pose_atual in poses:
                continue
            
            # se o usuário estava em pé, define o índice de início da pose atual
            if seated_frames == 0:
                first_seat = index
            seated_frames += 1
            
            # se o número de frames em que o usuário está sentado superar o threshold,
            # considera que ele está sentado e marca o índice de início da pose atual
            if seated_frames > seated_frames_threshold:
                poses[pose_atual] = {}
                poses[pose_atual]['start'] = first_seat
        
        else:  # não está sentado
            seated_frames = 0
            # se o usuário estava sentado, marca o índice de fim da pose atual
            if pose_atual in poses:
                if 'end' not in poses[pose_atual]:
                    poses[pose_atual]['end'] = index

                    if pose_atual == 4:
                        pose_atual += 3
                    else:
                        pose_atual += 1  # vai para a próxima pose
    
    return poses


# Poses para cada um
poses_vanessa = check_poses_vanessa(df_poses_vanessa)
poses_bruno = check_poses(df_poses_bruno)
poses_laguardia = check_poses(df_poses_laguardia)

In [90]:
# gráfico de linhas com as poses
fig = px.line(df_poses_bruno, x=df_poses_bruno.index, y=df_poses_bruno.columns)

for pose in poses_bruno.values():
    fig.add_vrect(x0=pose['start'], x1=pose['end'], fillcolor="green", opacity=0.25, line_width=0)

fig.show()

In [91]:
# cria um dataframe de cada pessoa com as poses catalogadas
df_poses_cat_vanessa = df_poses_vanessa.copy()
df_poses_cat_vanessa['pose'] = 0
for pose, indices in poses_vanessa.items():
    df_poses_cat_vanessa.loc[indices['start']:indices['end'], 'pose'] = pose

df_poses_cat_bruno = df_poses_bruno.copy()
df_poses_cat_bruno['pose'] = 0
for pose, indices in poses_bruno.items():
    df_poses_cat_bruno.loc[indices['start']:indices['end'], 'pose'] = pose

df_poses_cat_laguardia = df_poses_laguardia.copy()
df_poses_cat_laguardia['pose'] = 0
for pose, indices in poses_laguardia.items():
    df_poses_cat_laguardia.loc[indices['start']:indices['end'], 'pose'] = pose

# concatena os dataframes
df_poses_cat = pd.concat([df_poses_cat_vanessa, df_poses_cat_bruno, df_poses_cat_laguardia])

In [92]:
pprint.pprint(df_poses_cat_vanessa.value_counts('pose'))

pose
2     999
0     808
1     630
7     629
11    624
10    623
12    617
3     615
8     605
9     539
4     471
dtype: int64


In [93]:
# Dados da captura livre de poses Vanessa
df_aux_vanessa = df.copy()

df_aux_vanessa['pose'] = 0

df_aux_vanessa["pose"][19172-274:19510-274]= 3

df_aux_vanessa["pose"][19510-274:20392-274] = 1

df_aux_vanessa["pose"][20392-274:21766-274]= 3

df_aux_vanessa["pose"][21766-274:21980-274] = 1

df_aux_vanessa["pose"][21980-274:22552-274] = 8

df_aux_vanessa["pose"][22552-274:22933-274] = 7

poses_vanessa_livre = df_aux_vanessa.iloc[19172-274:22933-274, :]


In [94]:
df_aux_laguardia = df.copy()

df_aux_laguardia['pose'] = 0

# df_aux_laguardia["pose"][22690:23938] = 1

df_aux_laguardia["pose"][22690:23028] = 1

df_aux_laguardia["pose"][23028:23938] = 1
# talvez pose 4 e 5 no meio
df_aux_laguardia["pose"][23938:24383] = 4 #5 #1
# talvez pose 4 e 5 no meio
df_aux_laguardia["pose"][24383:24437] = 7 

df_aux_laguardia["pose"][24437:24745] = 7 #12

df_aux_laguardia["pose"][24745:24883] = 1 # 5

df_aux_laguardia["pose"][24883:25075] = 12 # 1

df_aux_laguardia["pose"][25075:25876] = 1
# talvez pose 4 no meio
df_aux_laguardia["pose"][25876:26332] = 3
# talvez pose 4 no meio
df_aux_laguardia["pose"][26332:26416] = 5

df_aux_laguardia["pose"][26416:26466] = 4 

poses_laguardia_livre = df_aux_laguardia.iloc[22690:26466, :]


In [95]:
poses_laguardia_livre.head()
# poses_laguardia_livre.to_csv('poses_livre_laguardia.csv', index=False)

p00  p01  p02  p03   p04   p05  p06   p07  p08  p09  \
index                                                                          
2023-05-19 19:13:05.424    0    0    0    0  1484  1859  275  3949  694  342   
2023-05-19 19:13:05.924    0    0    0    0  1512  1814  291  3950  737  347   
2023-05-19 19:13:06.424    0    0    0    0  1553  1791  297  3935  760  351   
2023-05-19 19:13:06.924    0    0    0    0  1563  1792  298  3935  775  355   
2023-05-19 19:13:07.424    0    0    0    0  1542  1812  299  3950  785  368   

                         p10  p11  pose  
index                                    
2023-05-19 19:13:05.424  123    0     1  
2023-05-19 19:13:05.924   78    0     1  
2023-05-19 19:13:06.424  122    0     1  
2023-05-19 19:13:06.924  130    0     1  
2023-05-19 19:13:07.424   94    0     1

In [96]:
# Dados da captura livre de poses Bruno
# Tempo convertido:
# 18:04:50 - 18:07:55 - Pose 2
# 18:07:55 - 18:11:20 - Pose 1
# 18:11:20 - 18:11:22 - Pose 2 - (transição da 1 pra 3)
# 18:11:22 - 18:14:28 - Pose 3
# 18:14:28 - 18:14:29 - Pose 1
# 18:14:29 - 18:18:16 - Pose 7
# 18:18:16 - 18:18:17 - Pose 0 - (uma transição muito esquisita)
# 18:18:17 - 18:18:18 - Pose 1 - (uma transição muito esquisita)
# 18:18:18 - 18:18:19 - Pose 8 - (uma transição muito esquisita)
# 18:18:19 - 18:20:58 - Pose 8
# 18:20:58 - 18:21:00 - Pose 12 - (quase a pose 12 mas ta mto esquisita)
# 18:21:00 - 18:21:12 - Pose 8 - (deixei o braço esquerdo forçando a cadeira pra tras, na pose 8)
# 18:21:12 - 18:22:29 - Pose 8
# 18:22:29 - 18:24:23 - Pose 1
# 18:24:23 - 18:24:26 - Pose 10 - (transição da 1 pra 10)
# 18:24:26 - 18:27:16 - Pose 10
# 18:27:16 - 18:27:17 - Pose 0 - (transição da 10 pra 1)
# 18:27:17 - 18:27:19 - Pose 1 - (transição da 10 pra 1)
# 18:27:19 - (até desligar) - Pose 1

df2 = pd.read_csv('data 19-05.csv')

# transforma o índice em datetime
df2.index = pd.to_datetime(df2['index'], format='%Y-%m-%dT%H:%M:%S.%f')
df2.drop(columns=['index'], inplace=True)

df_aux_bruno = df2.copy()

df_aux_bruno['pose'] = 0

df_aux_bruno["pose"][16399:16767] = 2

df_aux_bruno["pose"][16767:17177] = 1

df_aux_bruno["pose"][17177:17183] = 2

df_aux_bruno["pose"][17183:17553] = 3

df_aux_bruno["pose"][17553:17557] = 1

df_aux_bruno["pose"][17557:18009] = 7

df_aux_bruno["pose"][18009:18011] = 0

df_aux_bruno["pose"][18011:18013] = 1

df_aux_bruno["pose"][18013:18015] = 8

df_aux_bruno["pose"][18015:18333] = 8

df_aux_bruno["pose"][18333:18337] = 12

df_aux_bruno["pose"][18337:18363] = 8

df_aux_bruno["pose"][18363:18515] = 8

df_aux_bruno["pose"][18515:18743] = 1

df_aux_bruno["pose"][18743:18749] = 7 #10

df_aux_bruno["pose"][18749:19089] = 7 #10

df_aux_bruno["pose"][19089:19093] = 0

df_aux_bruno["pose"][19093:19097] = 1

df_aux_bruno["pose"][19097:19141] = 1

poses_bruno_livre = df_aux_bruno.iloc[16399:19141, :]

### Classificando poses

In [97]:
from sklearn.model_selection import train_test_split
from sklearn.neural_network import MLPClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.gaussian_process.kernels import RBF, DotProduct, Matern, WhiteKernel
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import classification_report, accuracy_score

# separa os dados de treino e teste

X = df_poses_cat.drop(columns=['pose'])
y = df_poses_cat['pose']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=.2, random_state=48)


# Treino e teste com os dados de Vanessa
X_vane = df_poses_cat_vanessa.drop(columns=['pose'])
y_vane = df_poses_cat_vanessa['pose']
X_train_vane, X_test_vane, y_train_vane, y_test_vane = train_test_split(X_vane, y_vane, test_size=.2, random_state=48)


# Treino e teste com os dados de Bruno
X_bruno = df_poses_cat_bruno.drop(columns=['pose'])
y_bruno = df_poses_cat_bruno['pose']
X_train_bruno, X_test_bruno, y_train_bruno, y_test_bruno = train_test_split(X_bruno, y_bruno, test_size=.2, random_state=48)


# Treino e teste com os dados de Laguardia
# X_laguardia = df_poses_cat_laguardia.drop(columns=['pose'])
# y_laguardia = df_poses_cat_laguardia['pose']
# X_train_laguardia, X_test_laguardia, y_train_laguardia, y_test_laguardia = train_test_split(X_laguardia, y_laguardia, test_size=.2, random_state=48)


# X_train = X_vane
# y_train = y_vane
# X_test = poses_vanessa_livre.drop(columns=['pose'])
# y_test = poses_vanessa_livre['pose']

# X_train = X_bruno
# y_train = y_bruno
# X_test = poses_bruno_livre.drop(columns=['pose'])
# y_test = poses_bruno_livre['pose']


# X_train = X_laguardia
# y_train = y_laguardia
X_test = poses_laguardia_livre.drop(columns=['pose'])
y_test = poses_laguardia_livre['pose']

print(f'X_train: {X_train.shape}')
print(f'X_test: {X_test.shape}')

X_train: (19362, 12)
X_test: (3775, 12)


In [98]:
# Lista de modelos a serem testados
models = [
    MLPClassifier(),
    KNeighborsClassifier(),
    DecisionTreeClassifier(),
    RandomForestClassifier(),
    AdaBoostClassifier(),
    GaussianNB(),
    QuadraticDiscriminantAnalysis()
]

# Lista de parâmetros 
param_grids = [
    # MLPClassifier
    {
        'hidden_layer_sizes': [(10,), (50,), (100,)],
        'activation': ['relu'],
        'alpha': [0.0001, 0.001, 0.01],
        'learning_rate': ['constant', 'adaptive'],
        'max_iter': [300, 500]
    },
    # KNeighborsClassifier
    {
        'n_neighbors': [3, 5, 7],
        'weights': ['uniform', 'distance'],
        'p': [1, 2, 3]
    },
    # DecisionTreeClassifier
    {
        'criterion': ['gini', 'entropy'],
        'max_depth': [None, 5, 10],
        'min_samples_split': [2, 5, 10]
    },
    # RandomForestClassifier
    {
        'n_estimators': [10, 50, 100],
        'max_depth': [None, 5, 10],
        'min_samples_split': [2, 5, 10]
    },
    # AdaBoostClassifier
    {
        'n_estimators': [50, 100, 200],
        'learning_rate': [0.1, 0.5, 1.0],
        'algorithm': ['SAMME', 'SAMME.R']
    },
    # GaussianNB
    {
        'var_smoothing': [1e-9, 1e-8, 1e-7]
    },
    # QuadraticDiscriminantAnalysis
    {
        'reg_param': [0.0, 0.1, 0.5, 1.0]
    }
]

In [99]:
# Cria e treina a grid de busca
for model, param_grid in zip(models, param_grids):
    break
    print(f'Treinando {model.__class__.__name__}')
    grid = GridSearchCV(model, param_grid, scoring='accuracy', refit='accuracy', verbose=1, cv=2)
    grid.fit(X_train, y_train)
    print(f'Melhores parâmetros: {grid.best_params_}')
    print(f'Melhor score: {grid.best_score_}')
    print(f'Score no teste: {grid.score(X_test, y_test)}')
    print('')

In [100]:
# Treina a árvore de decisão com os melhores parâmetros
model_tree = DecisionTreeClassifier(criterion='entropy', max_depth=None, min_samples_split=10)
model_tree.fit(X_train, y_train)
print(f'Score no treino: {model_tree.score(X_train, y_train)}')
print(f'Score no teste: {model_tree.score(X_test, y_test)}')

# Mosta a importância de cada feature
print('Importância das features:')
for feature, importance in zip(X_train.columns, model_tree.feature_importances_):
    print(f'{feature}: {importance}')

Score no treino: 0.99437041627931
Score no teste: 0.25589403973509933
Importância das features:
p00: 0.12416393729631267
p01: 0.03856270581124787
p02: 0.02602407653698714
p03: 0.0013075865461178347
p04: 0.04527669471592979
p05: 0.1799499247864961
p06: 0.22025290335852435
p07: 0.18421963957499116
p08: 0.006198358219141312
p09: 0.03649159518263734
p10: 0.08385466467413097
p11: 0.05369791329748344


In [101]:
# Cria o modelo de Random Forest com os melhores parâmetros
model_rf = RandomForestClassifier(max_depth=None, min_samples_split=5, n_estimators=100)
model_rf.fit(X_train, y_train)

# Mostra o score no treino
print(f'Score no treino: {model_rf.score(X_train, y_train)}')

# Mostra o score no teste
print(f'Score no teste: {model_rf.score(X_test, y_test)}')

# Prediz todos os dados catalogados
# df_poses_cat['pose_pred'] = model_rf.predict(X)

Score no treino: 0.9990186964156595
Score no teste: 0.6397350993377483


In [103]:
poses_laguardia_livre['pose_pred'] = model_rf.predict(X_test)

C:\Users\vanes\AppData\Local\Temp\ipykernel_9592\1063243247.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [104]:
# Mostra o resultado nos dados catalogados
fig = px.line(poses_laguardia_livre, x=poses_laguardia_livre.index, y=['pose_pred', 'pose'])
fig.show()

In [ ]:
poses_vanessa_livre['pose'].value_counts()

3    1712
1    1096
8     572
7     381
Name: pose, dtype: int64